<a href="https://colab.research.google.com/github/indriaramadhani/Indri-s-quantitative-research-portfolio/blob/main/FM_GA_2_MC.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [ ]:
!pip install numba_stats
import numpy as np
import plotly.express as px
import pandas as pd
from math import log, sqrt, exp, pi
from dataclasses import dataclass
from numba_stats import norm, uniform
from warnings import simplefilter
simplefilter(action="ignore", category=pd.errors.PerformanceWarning)

In [ ]:
def sum2(x,y):
 z=x+y
 return(z)
z=sum2(2,4)
print(" x+y = ", z)

 x+y =  6


In [ ]:
S=58.51
K=35.0
σ=0.06
q=0.0
r=0.05
T= 365/365 # in Days
Nstep=60
Nsim=600
def GBMSim(S,K,σ,r,q,T,Nstep,Nsim):
  """
  dS_t = rS_tdt + σ*S_tdZ_t)
  S_t = S_0 exp((r-0.5σ^2)*(t) + σ*sqrt(t) Ɛ_t)
  """
  dt = T/Nstep
  drift=r-q-0.5*σ*σ
  S_M=np.zeros((Nstep+1,Nsim))
  S_M[0,:]=np.ones(Nsim)*S
  np.random.seed(0)
  Ɛ=np.random.randn(Nstep,Nsim)
  for i in range(1,Nstep+1):
    S_M[i,:]=S_M[0,:]*np.exp(drift*dt*i + σ*np.sqrt(dt*i)*Ɛ[i-1,:])
  return S_M
SV=GBMSim(S,K,σ,r,q,T,Nstep,Nsim)


In [ ]:
fig = px.scatter(SV,labels={"value":"Value of S", "variable":"Paths"})
fig.update_layout(showlegend=False)
fig.show()

In [ ]:
def MC_Call(S_M,K,r,T):
  ST=+S_M[-1]
  payoff=np.maximum(ST-K,0)
  return np.exp(-r*T)*np.mean(payoff)

In [ ]:
call=MC_Call(SV,K,r,T)
call

25.254430080350364

In [ ]:
@dataclass
class BSM_OptionPrices:
  S: float = 58.51
  K: float = 35.0
  σ: float = 0.06
  q: float = 0.0
  r: float = 0.05
  T: float = 365/365

  @staticmethod
  def N(x) -> float:
    return norm.cdf(x,0.0,1.0)

  @staticmethod
  def n(x) -> float:
    return norm.pdf(x,0.0,1.0)

  def d1_Func(m) -> float:
    S, K, σ, r, q, T=m.S, m.K, m.σ, m.r, m.q, m.T
    d1 = ((log(S/K) + (r-q + 0.5 * σ *σ) * T)/ (σ * sqrt(T)))
    return d1

  def d2_Func(m) -> float:
    σ, T = m.σ, m.T
    d1 = m.d1_Func()
    d2 = d1-σ * sqrt(T)
    return d2

  def CallPrice(m)  -> float:
    S, K, r, q, T=m.S, m.K, m.r, m.q, m.T
    d1 = m.d1_Func()
    d2 = m.d2_Func()
    Price=S*exp(-q*T)*m.N(d1)-K*exp(-r*T)*m.N(d2)
    return Price

  def PutPrice(m)  -> float:
    S, K, σ, r, q, T=m.S, m.K, m.σ, m.r, m.q, m.T
    d1 = m.d1_Func()
    d2 = m.d2_Func()
    Price=K*exp(-r*T)*m.N(-d2)-S*exp(-q*T)*m.N(-d1)
    return Price

In [ ]:
BSM=BSM_OptionPrices()
bsmcall=BSM.CallPrice()
mccall=MC_Call(SV,K,r,T)
[bsmcall,mccall]

[25.216970142475006, 25.254430080350364]

# Multi Asset Simulation

In [ ]:
Nsim=60
e=np.random.normal(size=(Nsim,2))
fig=px.line(e)
fig.show()

In [ ]:
rho=0.95
eh=np.zeros((Nsim,2))
eh[:,0]=rho*e[:,0]
eh[:,1]=rho*e[:,0]+np.sqrt(1-rho**2)*e[:,1]
fig=px.line(eh)
fig.show()

In [ ]:
def GBM_MA(S0V,μV,qV,σV,ρM,T,Nsim,Nstep):
  dt = T/Nstep
  N = len(S0V)
  cR=np.linalg.cholesky(ρM)
  S_V=np.zeros([Nsim,Nstep+1,N])
  S_V[:,0,:]=S0V*np.ones([Nsim,N])
  for i in range(1,Nstep+1):
    eV=np.random.normal(size=(Nsim,N))
    eVc=(np.matmul(eV,cR))
    S_V[:,i,:]=S_V[:,0,:]*np.exp((μV-qV-0.5*σV*σV)*dt*i+σV*np.sqrt(dt*i)*eVc)
  return(S_V)

T=30/365
Nsim=2000
Nstep=50
S0V=np.array([100,50])
μV=np.array([0.05,0.10])
qV=np.array([0.0,0.0])
σV=np.array([0.25,0.15])
ρM=np.array([[1.0,-0.20],[-0.2,1.0]])
S_V=GBM_MA(S0V,μV,qV,σV,ρM,T,Nsim,Nstep)
fig=px.line(np.transpose(S_V[:,:,0]))
fig.update_layout(showlegend=False)
fig.show()

In [ ]:
fig=px.line(np.transpose(S_V[:,:,1]))
fig.update_layout(showlegend=False)
fig.show()

#Monte Carlo Simulation and DCF Valuation

In [ ]:
years = ['2023A', '2024P', '2025P', '2026P', '2027P', '2028P']
sales = pd.Series(index=years)
sales['2023A'] = 45.75
sales

2023A    45.75
2024P      NaN
2025P      NaN
2026P      NaN
2027P      NaN
2028P      NaN
dtype: float64

In [ ]:
growth_rate = 0.085
for year in range(1, 6):
    sales[year] = sales[year - 1] * (1 + growth_rate)
sales

2023A    45.750000
2024P    49.638750
2025P    53.858044
2026P    58.435977
2027P    63.403036
2028P    68.792294
dtype: float64

In [ ]:
EBITDA_m = 0.34
depr_pct = 0.01
ebitda = sales * EBITDA_m
depreciation = sales * depr_pct
ebit = ebitda - depreciation
nwc_percent = 0.0324
nwc = sales * nwc_percent
change_in_nwc = nwc.shift(1) - nwc
CAPEX_pct = depr_pct
CAPEX = -(sales * CAPEX_pct)
tax_rate = 0.174
tax_payment = -ebit * tax_rate
tax_payment = tax_payment.apply(lambda x: min(x, 0))
free_cash_flow = ebit + depreciation + tax_payment + CAPEX + change_in_nwc
free_cash_flow

2023A          NaN
2024P    13.404535
2025P    14.543920
2026P    15.780154
2027P    17.121467
2028P    18.576791
dtype: float64

In [ ]:
cost_of_capital = 0.8
terminal_growth = 0.21
terminal_value = ((free_cash_flow[-1] * (1 + terminal_growth)) /
                 (cost_of_capital - terminal_growth))
discount_factors = [(1 / (1 + cost_of_capital)) ** i for i in range (1,6)]
dcf_value = (sum(free_cash_flow[1:] * discount_factors) +
            terminal_value * discount_factors[-1])
print(dcf_value)

19.271965093619777


In [ ]:
output = pd.DataFrame([sales, ebit, free_cash_flow],
                     index=['Sales', 'EBIT', 'Free Cash Flow']).round(1)
output

2023A  2024P  2025P  2026P  2027P  2028P
Sales            45.8   49.6   53.9   58.4   63.4   68.8
EBIT             15.1   16.4   17.8   19.3   20.9   22.7
Free Cash Flow    NaN   13.4   14.5   15.8   17.1   18.6

In [ ]:
iterations = 10000
def run_mcs():

    # Create probability distributions
    sales_growth_dist = np.random.normal(loc=0.1, scale=0.01, size=iterations)
    EBITDA_m_dist = np.random.normal(loc=0.14, scale=0.02, size=iterations)
    nwc_percent_dist = np.random.normal(loc=0.24, scale=0.01, size=iterations)

    # Calculate DCF value for each set of random inputs
    output_distribution = []
    for i in range(iterations):
        for year in range(1, 6):
            sales[year] = sales[year - 1] * (1 + sales_growth_dist[0])
        EBITDA = sales * EBITDA_m_dist[i]
        depreciation = (sales * depr_pct)
        ebit = EBITDA - depreciation
        nwc = sales * nwc_percent_dist[i]
        change_in_nwc = nwc.shift(1) - nwc
        CAPEX = -(sales * CAPEX_pct)
        tax_payment = -ebit * tax_rate
        tax_payment = tax_payment.apply(lambda x: min(x, 0))
        free_cash_flow = ebit + depreciation + tax_payment + CAPEX + change_in_nwc

        # DCF valuation
        terminal_value = (free_cash_flow[-1] * 1.02) / (cost_of_capital - 0.02)
        free_cash_flow[-1] += terminal_value
        discount_factors = [(1 / (1 + cost_of_capital)) ** i for i in range (1,6)]
        dcf_value = sum(free_cash_flow[1:] * discount_factors )
        output_distribution.append(dcf_value)

    return output_distribution

In [ ]:
run_mcs()

[6.341470427773264,
 6.459355692389592,
 6.465551616994784,
 6.3910531321380315,
 4.9810147457375,
 6.122223477870769,
 4.04888532748368,
 3.806844161906526,
 5.95961378221028,
 6.436056246811693,
 7.316671489948289,
 6.537348504571318,
 5.788455130143283,
 5.200398753574059,
 7.231418313645414,
 5.828003647744284,
 5.777086978635091,
 5.715658425188674,
 6.107584876052739,
 6.856142667190434,
 7.70414420885137,
 5.563044467176023,
 5.1160098135044585,
 5.89109253244024,
 7.6486800299156315,
 6.389386929533251,
 5.887451585009092,
 5.56315376689686,
 6.90727603031687,
 6.3723913738140965,
 5.79726984672993,
 4.667722660958672,
 6.807982950888137,
 6.3584694145347,
 7.112251161215306,
 5.962589944391435,
 4.678108884564666,
 7.357962043529385,
 5.293761518610455,
 8.51681658763852,
 7.139890224626269,
 5.330850756888202,
 6.0334606572439995,
 5.062097376527081,
 5.092290476251459,
 6.8239110789919994,
 4.341002833694787,
 4.145880652452122,
 7.100765937350701,
 7.002880451626229,
 6.270

In [ ]:
EV=run_mcs()
fig = px.histogram(EV)
fig.show()

In [ ]:
@dataclass
class DCF_MCS:
  years = ['2023A', '2024P', '2025P', '2026P', '2027P', '2028P']
  g: float = 0.085 # Growth rate
  EBITDA_m: float = 0.34
  depr_pct: float = 0.01
  nwc_percent: float = 0.034
  tax_rate: float = 0.174
  cost_of_capital: float = 0.8
  terminal_growth: float = 0.21
  Nsim: int = 10000

  def DCF(m):
    for year in range(1, 6):
      sales[year] = sales[year - 1] * (1 + m.g)
    ebitda = sales * m.EBITDA_m
    depreciation = (sales * m.depr_pct)
    CAPEX_pct = m.depr_pct
    ebit = ebitda - depreciation
    nwc = sales * m.nwc_percent
    change_in_nwc = nwc.shift(1) - nwc
    CAPEX = -(sales * CAPEX_pct)
    tax_payment = -ebit * m.tax_rate
    tax_payment = tax_payment.apply(lambda x: min(x, 0))
    free_cash_flow = ebit + depreciation + tax_payment + CAPEX + change_in_nwc
    output = pd.DataFrame([sales, ebit, free_cash_flow],
                     index=['Sales', 'EBIT', 'Free Cash Flow']).round(1)
    return(output)

  def DCFsim(m):
    sales = pd.Series(index=m.years)
    sales['2023A'] = 45.75
  # Create probability distributions
    sales_growth_dist = np.random.normal(loc=m.g, scale=0.01, size=m.Nsim)
    EBITDA_m_dist = np.random.normal(loc=m.EBITDA_m, scale=0.02, size=m.Nsim)
    nwc_percent_dist = np.random.normal(loc=m.nwc_percent, scale=0.01, size=m.Nsim)

    # Calculate DCF value for each set of random inputs
    output_distribution = []
    for i in range(m.Nsim):
        for year in range(1, 6):
            sales[year] = sales[year - 1] * (1 + sales_growth_dist[0])
        ebitda = sales * EBITDA_m_dist[i]
        depreciation = (sales * m.depr_pct)
        CAPEX_pct = m.depr_pct
        ebit = ebitda - depreciation
        nwc = sales * nwc_percent_dist[i]
        change_in_nwc = nwc.shift(1) - nwc
        CAPEX = -(sales * CAPEX_pct)
        tax_payment = -ebit * m.tax_rate
        tax_payment = tax_payment.apply(lambda x: min(x, 0))
        free_cash_flow = ebit + depreciation + tax_payment + CAPEX + change_in_nwc

        # DCF valuation
        terminal_value = (free_cash_flow[-1] * (1.0+m.terminal_growth)) / (m.cost_of_capital - m.terminal_growth)
        free_cash_flow[-1] += terminal_value
        discount_factors = [(1 / (1 + m.cost_of_capital)) ** i for i in range (1,6)]
        dcf_value = sum(free_cash_flow[1:] * discount_factors )
        output_distribution.append(dcf_value)

    return output_distribution

In [ ]:
  NPV=DCF_MCS()
  table=NPV.DCF()
  print(table)
  values=NPV.DCFsim()

                2023A  2024P  2025P  2026P  2027P  2028P
Sales            45.8   49.6   53.9   58.4   63.4   68.8
EBIT             15.1   16.4   17.8   19.3   20.9   22.7
Free Cash Flow    NaN   13.4   14.5   15.8   17.1   18.6


In [ ]:
fig=px.histogram(np.transpose(values))
fig.update_layout(showlegend=False)
fig.show()